Spatial Visualization of Subbasin-Predictions

In [20]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append('../..')
import os
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt 
from src import load_data, evaluate, datasets, utils, stgcn
import random
import pickle
import json
import networkx as nx
import folium
import branca.colormap as cm
import shapely
from shapely.geometry import shape

np.random.seed(0)
random.seed(0)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [21]:
results = pickle.load(open('../../pickle/results/STGCN_simulationTraining_{}.pkl'.format('20190830-182512'), 'rb'))
subbasin_shapes = load_data.load_subbasin_shapes()

test_subbasins = results[results['is_test_subbasin']]['subbasin'].unique()
train_subbasins = results[~results['is_test_subbasin']]['subbasin'].unique()
station_subbasins = results[~pd.isna(results['actual'])]['subbasin'].unique()

subbasin_graph = utils.create_subbasin_graph()
component_graph = subbasin_graph.copy()
component_graph.remove_nodes_from(['sub-1', 'sub1', 'sub474', 'sub475'])  # remove Lake Erie and sink to get connected components
connected_components = sorted(sorted(c) for c in nx.connected_components(nx.Graph(component_graph)))

component_outlines = []
for component in connected_components:
    comp_outline = shape(subbasin_shapes[int(component[0][3:])]['geometry'])
    for subbasin in component[1:]:
        comp_outline = comp_outline.union(shape(subbasin_shapes[int(subbasin[3:])]['geometry']))
    component_outlines.append(comp_outline)
component_geojson = json.loads(json.dumps({'type':'FeatureCollection', 'features': [shapely.geometry.mapping(o) for o in component_outlines]}))
def get_component(subbasin):
    for i, com in enumerate(connected_components):
        if 'sub' + str(int(subbasin)) in com:
            return i
    return -1

In [22]:
for subbasin in results['subbasin'].unique():
    subbasin_results = results[results['subbasin']==subbasin].set_index('date')
    group = 'test' if subbasin_results['is_test_subbasin'].iloc[0] else 'train'
    if subbasin_results['simulated_streamflow'].min() - subbasin_results['simulated_streamflow'].max() == 0:
        nse_sim = np.nan
    else:
        nse_sim = evaluate.evaluate_daily('sub' + str(subbasin), subbasin_results['prediction'], subbasin_results['simulated_streamflow'], group=group)[0]
    nse = np.nan
    if not pd.isna(subbasin_results['actual'].iloc[0]):
        station = subbasin_results['station'].iloc[0]
        nse = evaluate.evaluate_daily(station, subbasin_results['prediction'], subbasin_results['actual'], group=group)[0]
    subbasin_shapes[subbasin]['properties']['NSE (sim)'] = nse_sim
    subbasin_shapes[subbasin]['properties']['NSE'] = nse
    subbasin_shapes[subbasin]['properties']['group'] = group
    subbasin_shapes[subbasin]['properties']['component'] = get_component(subbasin)

def cmap(nse):
    return cm.LinearColormap(['red', 'yellow', 'green'], vmin=-1, vmax=1)(nse) if not pd.isna(nse) else '#000'

In [23]:
m = folium.Map(location=[42.1, -81.4], zoom_start=6, height='70%')
folium.GeoJson(data=json.dumps(component_geojson), name='components',
               style_function=lambda f : {'fillOpacity': 0, 'color': 'blue', 'weight': 4}).add_to(m)

folium.GeoJson(data={'type':'FeatureCollection', 'features': [s for k,s in subbasin_shapes.items() if k in train_subbasins]},
               style_function=lambda feature: {'fillColor': cmap(subbasin_shapes[feature['properties']['SubId']]['properties']['NSE (sim)']), 
                                               'color': 'black', 'weight': 0.5, 'fillOpacity': 0.5, 'line_opacity': 0.1,},
               tooltip=folium.features.GeoJsonTooltip(fields=['SubId', 'DowSubId', 'NSE (sim)', 'NSE', 'component', 'group']), name='train NSE (sim)').add_to(m)
folium.GeoJson(data={'type':'FeatureCollection', 'features': [s for k,s in subbasin_shapes.items() if k in test_subbasins]},
               style_function=lambda feature: {'fillColor': cmap(subbasin_shapes[feature['properties']['SubId']]['properties']['NSE (sim)']), 
                                               'color': 'black', 'weight': 0.5, 'fillOpacity': 0.5, 'line_opacity': 0.1,},
               tooltip=folium.features.GeoJsonTooltip(fields=['SubId', 'DowSubId', 'NSE (sim)', 'NSE', 'component', 'group']), name='test NSE (sim)').add_to(m)
folium.GeoJson(data={'type':'FeatureCollection', 'features': [s for k,s in subbasin_shapes.items() if k in station_subbasins]},
               style_function=lambda feature: {'fillColor': cmap(subbasin_shapes[feature['properties']['SubId']]['properties']['NSE']), 
                                               'color': 'black', 'weight': 0.5, 'fillOpacity': 0.5, 'line_opacity': 0.1,}, name='station NSE').add_to(m)

folium.LayerControl().add_to(m)
m